# 10-714 Homework 4

In this homework, you will leverage all of the components built in the last three homeworks to solve some modern problems with high performing network structures. We will start by adding a few new ops leveraging our new CPU/CUDA backends. Then, you will implement convolution, and a convolutional neural network to train a classifier on the CIFAR-10 image classification dataset. Then, you will implement recurrent and long-short term memory (LSTM) neural networks, and do word-level prediction language modeling on the Penn Treebank dataset.

As always, we will start by copying this notebook and getting the starting code.
Reminder: __you must save a copy in drive__.

In [1]:
import sys
sys.path.append('./python')
import needle as ndl

In [2]:
ndl.cuda().enabled()  # 

True

In [3]:
ndl.cuda()            # 本质是BackDevice对象, 含导入的.so包。 enable（）返回cuda.so包是否存在

cuda()

In [2]:
# Imperative automatic differentiation    对比声明式declarative programming
v1=ndl.Tensor([1])
v2=ndl.exp(v1)
v3=v2 + 1
v4=v2 * v3
# Executes computation as we construct the computational graph
# Allow easy mixing of python control flow and construction
if v4.numpy() > 0.5:
    v5 = v4 * 2
else:
    v5 = v4
v5.backward()

In [3]:
v1.grad

needle.Tensor([34.99279])

In [4]:
import torch
a=torch.tensor(1)
a

tensor(1)

In [ ]:
# Code to set up the assignment
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/MyDrive/
!mkdir -p 10714
%cd /content/drive/MyDrive/10714
!git clone https://github.com/dlsys10714/hw4.git
%cd /content/drive/MyDrive/10714/hw4

!pip3 install --upgrade --no-deps git+https://github.com/dlsys10714/mugrade.git
!pip3 install pybind11

In [9]:
!make

-- The C compiler identification is GNU 9.4.0
-- The CXX compiler identification is GNU 9.4.0
-- The CUDA compiler identification is NVIDIA 11.1.74
-- Check for working C compiler: /usr/bin/cc
-- Check for working C compiler: /usr/bin/cc -- works
-- Detecting C compiler ABI info
-- Detecting C compiler ABI info - done
-- Detecting C compile features
-- Detecting C compile features - done
-- Check for working CXX compiler: /usr/bin/c++
-- Check for working CXX compiler: /usr/bin/c++ -- works
-- Detecting CXX compiler ABI info
-- Detecting CXX compiler ABI info - done
-- Detecting CXX compile features
-- Detecting CXX compile features - done
-- Check for working CUDA compiler: /usr/local/cuda/bin/nvcc
-- Check for working CUDA compiler: /usr/local/cuda/bin/nvcc -- works
-- Detecting CUDA compiler ABI info
-- Detecting CUDA compiler ABI info - done
-- Found Python: /home/xuweijia/.conda/envs/pytorch1.9/bin/python3.9 (found version "3.9.6") found components: Development Interpreter 
-- Per

In [3]:
import sys
sys.path.append('./python')

In [3]:
# Download the datasets you will be using for this assignment

import urllib.request
import os

!mkdir -p './data/ptb'
# Download Penn Treebank dataset
ptb_data = "https://raw.githubusercontent.com/wojzaremba/lstm/master/data/ptb."
for f in ['train.txt', 'test.txt', 'valid.txt']:
    if not os.path.exists(os.path.join('./data/ptb', f)):
        urllib.request.urlretrieve(ptb_data + f, os.path.join('./data/ptb', f))

In [1]:
# Download CIFAR-10 dataset
if not os.path.isdir("./data/cifar-10-batches-py"):
    urllib.request.urlretrieve("https://www.cs.toronto.edu/~kriz/cifar-10-python.tar.gz", "./data/cifar-10-python.tar.gz")
    !tar -xvzf './data/cifar-10-python.tar.gz' -C './data'

cifar-10-batches-py/
cifar-10-batches-py/data_batch_4
cifar-10-batches-py/readme.html
cifar-10-batches-py/test_batch
cifar-10-batches-py/data_batch_3
cifar-10-batches-py/batches.meta
cifar-10-batches-py/data_batch_2
cifar-10-batches-py/data_batch_5
cifar-10-batches-py/data_batch_1


To finish setting up the assignment, go ahead and fill in all the code in `python/needle/autograd.py` using your solution code from the previous homework.

## Part 1: ND Backend [10 pts]

Fill in the following classes in `python/needle/ops.py`:

- `PowerScalar`
- `EWiseDiv`
- `DivScalar`
- `Transpose`
- `Reshape`
- `BroadcastTo`
- `Summation`
- `MatMul`
- `Negate`
- `Log`
- `Exp`
- `ReLU`
- `LogSumExp`
- `Tanh` (new)
- `Stack` (new)
- `Split` (new)

Note that for most of these, you already wrote the solutions in the previous homework and you should not need to change your previous solution, however `TanhOp`, `Stack`, and `Split` are newly added. `Stack` concatenates same-sized tensors along a new axis, and `Split` undoes this operation. The gradients of the two operations can be written in terms of each other. We do not directly test `Split`, and only test the backward pass of `Stack` (for which we assume you used `Split`).

**Note:** You may want to make your Summation op support sums over multiple axes; you will likely need it for the backward pass of the BroadcastTo op if yours supports broadcasting over multiple axes at a time. However, this is more about ease of use than necessity, and we leave this decision up to you (there are no corresponding tests).

**Note:** Depending on your implementations, you may want to ensure that you call `.compact()` before reshaping arrays. (If this is necessary, you will run into corresponding error messages later in the assignment.)

In [4]:
!python3 -m pytest -l -v -k "nd_backend"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1637 deselected / 118 selected                          

tests/test_nd_backend.py::test_ewise_fn[cpu-shape0-divide] PASSED        [  0%]
tests/test_nd_backend.py::test_ewise_fn[cpu-shape0-subtract] PASSED      [  1%]
tests/test_nd_backend.py::test_ewise_fn[cpu-shape1-divide] PASSED        [  2%]
tests/test_nd_backend.py::test_ewise_fn[cpu-shape1-subtract] PASSED      [  3%]
tests/test_nd_backend.py::test_ewise_fn[cuda-shape0-divide] SKIPPED      [  4%]
tests/test_nd_backend.py::test_ewise_fn[cuda-shape0-subtract] SKIPPED    [  5%]
tests/test_nd_backend.py::test_ewise_fn[cuda-shape1-divide] SKIPPED      [  5%]
tests/test_nd_backend.py::test_ewise_fn[cuda-shape1-subtract] SKIPPED    [  6%]

tests/test_nd_backend.py::test_reshape[cpu-shape0-shape_to0] PASSED      [ 80%]
tests/test_nd_backend.py::test_reshape[cpu-shape1-shape_to1] PASSED      [ 81%]
tests/test_nd_backend.py::test_reshape[cuda-shape0-shape_to0] SKIPPED    [ 82%]
tests/test_nd_backend.py::test_reshape[cuda-shape1-shape_to1] SKIPPED    [ 83%]
tests/test_nd_backend.py::test_transpose[cpu-axes0-shape0] PASSED        [ 83%]
tests/test_nd_backend.py::test_transpose[cpu-axes0-shape1] PASSED        [ 84%]
tests/test_nd_backend.py::test_transpose[cpu-axes1-shape0] PASSED        [ 85%]
tests/test_nd_backend.py::test_transpose[cpu-axes1-shape1] PASSED        [ 86%]
tests/test_nd_backend.py::test_transpose[cpu-None-shape0] PASSED         [ 87%]
tests/test_nd_backend.py::test_transpose[cpu-None-shape1] PASSED         [ 88%]
tests/test_nd_backend.py::test_transpose[cuda-axes0-shape0] SKIPPED      [ 88%]
tests/test_nd_backend.py::test_transpose[cuda-axes0-shape1] SKIPPED      [ 89%]
tests/test_nd_backend.py::test_transpose

In [7]:
#!python3 -m mugrade submit _1wNPXusjlWR2gMjyo9we -k "new_nd_backend"

In [1]:
import numpy as np
import torch
shape=(1,5, 7)
axis=2
l=5
_A = [np.random.randn(*shape).astype(np.float32) for i in range(l)]
#A = [ndl.Tensor(nd.array(_A[i]), device=device) for i in range(l)]
A_t = [torch.Tensor(_A[i]) for i in range(l)]
#out = ndl.stack(A, axis=axis)
out_t = torch.stack(A_t, dim=axis)
out_t.numpy().shape

(1, 5, 5, 7)

In [19]:
A_t

[tensor([[ 0.5992, -1.1831,  0.8218,  0.5839,  0.2127],
         [-0.8875, -0.4803,  0.6391,  0.0665,  0.1593],
         [ 0.8032, -1.3329,  0.7208,  0.7276, -0.6443],
         [-0.1239,  1.2784, -0.0199,  0.6180, -0.8635],
         [-1.0180, -0.3801, -0.2203, -1.2172,  0.9371]]),
 tensor([[-1.7657, -0.2248, -0.7031,  0.1679, -0.2718],
         [ 1.3280,  0.2021, -0.9019, -0.5396,  0.6769],
         [ 0.8008, -0.2486,  2.1255, -0.1480,  0.3200],
         [-0.1431,  1.3699, -0.4018, -0.8857, -0.8230],
         [ 0.1218, -0.4963,  0.3788,  0.4658,  0.4811]])]

In [20]:
a=[3,4]
a.insert(1,5)
a

[3, 5, 4]

## Part 2: CIFAR-10 dataset [10 points]

Next, you will write support for the [CIFAR-10](https://www.cs.toronto.edu/~kriz/cifar.html) image classification dataset, which consists of 60,000 32x32 color images in 10 classes, with 6,000 images per class. There are 50k training images and 10k test images. 

Start by implementing the `__init__` function in the `CIFAR10Dataset` class. You can read in the link above how to properly read the CIFAR-10 dataset files you downloaded at the beginning of the homework. Also fill in `__getitem__` and `__len__`. Note that the return shape of the data from `__getitem__` should be in order (3, 32, 32).



In [12]:
!python3 -m pytest -l -v -k "cifar10"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1803 items / 1791 deselected / 12 selected                           

tests/test_cifar_ptb_data.py::test_cifar10_dataset[True] PASSED          [  8%]
tests/test_cifar_ptb_data.py::test_cifar10_dataset[False] PASSED         [ 16%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-True-1] PASSED     [ 25%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-True-15] PASSED    [ 33%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-False-1] PASSED    [ 41%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-False-15] PASSED   [ 50%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cuda-True-1] PASSED    [ 58%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cuda-True-15] PASSED   [ 66%]

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "cifar10"

## Part 3: Convolutional neural network [40 points]

Here's an outline of what you will do in this task.

In `python/needle/backend_ndarray/ndarray.py`, implement:
- `flip`
- `pad`

In `python/needle/ops.py`, implement (forward and backward):
- `Flip`
- `Dilate`
- `UnDilate`
- `Conv`

In `python/needle/nn.py`, implement:
- `Flatten`
- `Conv`

In `python/apps/models.py`, fill in the `ResNet9` class.  

In `apps/simple_training.py`, fill in:
- `epoch_general_cifar10`,
- `train_cifar10`
- `evaluate_cifar10`

We have provided a `BatchNorm2d` implementation for you as a wrapper around your previous `BatchNorm1d` implementation. 

### Padding ndarrays

Convolution as typically implemented in deep learning libraries cuts down the size of inputs;
e.g., a (1, 32, 32, 3) image convolved with a 3x3 filter would give a (1, 30, 30, c) output.
A way around this is to pad the input ndarray before performing convolution, e.g., pad with zeros to get a (1, 34, 34, 3) ndarray so that the result is (1, 32, 32, 3). 

Padding is also required for the backward pass of convolution.

You should implement `pad` in `ndarray.py` to closely reflect the behavior of `np.pad`.
That is, `pad` should take a tuple of 2-tuples with length equal to the number of dimensions of the array,
where each element in the 2-tuple corresponds to "left padding" and "right padding", respectively.

For example, if `A` is a (10, 32, 32, 8) ndarray (think NHWC), then `A.pad( (0, 0), (2, 2), (2, 2), (0, 0) )` would be a (10, 36, 36, 8) ndarray where the "spatial" dimension has been padded by two zeros on all sides.

In [ ]:
!python3 -m pytest -l -v -k "pad_forward"

-------------------------------------

### Flipping ndarrays & FlipOp

In [6]:
import numpy as np
import ctypes

Some utility code for a demonstration below which you can probably ignore. It might be instructive to check out the `offset` function.

In [7]:
# reads off the underlying data array in order (i.e., offset 0, offset 1, ..., offset n)
# i.e., ignoring strides
def raw_data(X):
    X = np.array(X) # copy, thus compact X
    return np.frombuffer(ctypes.string_at(X.ctypes.data, X.nbytes), dtype=X.dtype, count=X.size)  # X底层数据

# Xold and Xnew should reference the same underlying data
def offset(Xold, Xnew):
    assert Xold.itemsize == Xnew.itemsize
    # compare addresses to the beginning of the arrays
    return (Xnew.ctypes.data - Xold.ctypes.data)//Xnew.itemsize

def strides(X):
    return ', '.join([str(x//X.itemsize) for x in X.strides])

# 输入X在内存中的数据，输出(compact后的)
def format_array(X, shape):
    assert len(shape) == 3, "I only made this formatting work for ndims = 3"
    def chunks(l, n):
        n = max(1, n)
        return (l[i:i+n] for i in range(0, len(l), n))
    a = [str(x) if x >= 10 else ' ' + str(x) for x in X]
    a = ['(' + ' '.join(y) + ')' for y in [x for x in chunks(a, shape[-1])]]
    a = ['|' + ' '.join(y) + '|' for y in [x for x in chunks(a, shape[-2])]]
    return '  '.join(a)

def inspect_array(X, *, is_a_copy_of):
    # compacts X, then reads it off in order
    print('Data: %s' % format_array(raw_data(X), X.shape))
    # compares address of X to copy_of, thus finding X's offset
    print('Offset: %s' % offset(is_a_copy_of, X))       # 输入2array,共享同一底层数据。输出对应offset.
    print('Strides: %s' % strides(X))

In order to implement the backwards pass of 2D convolution, we will (probably) need a function which _flips_
axes of ndarrays. We say "probably" because you could probably cleverly implement your convolution forward
function to avoid this. However, we think it is easiest to think about this if you have the ability to "flip" the kernel along its vertical and horizontal dimensions.

We will try to build up your intuition for the "flip" operation below in order to help you figure out how to implement it in `ndarray.py`. To do that, we explore numpy's `np.flip` function below. One thing to note is that
`flip` is typically implemented by using negative strides and changing the _offset_ of the underlying array.

For example, flipping an array on _all_ of its axes is equivalent to reversing the array. In this case, you can imagine that we would want all the strides to be negative, and the offset to be the length of the array (to start at the end of the array and "stride" backwards).

Since we did not explicitly support negative strides in our implementation for the last homework, we will merely call `NDArray.make` with them to make our "flipped" array and then immediately call `.compact()`. Other than changing unsigned ints to signed ints in a few places, we suspect your existing `compact` function should not have to change at all to accomodate negative strides. In the .cc and .cu files we distributed, we have already changed the function signatures to reflect this.

Alternatively, you could simply implement `flip` in the CPU backend by copying memory, which you _may_ find more intuitive. We suggest following our mini tutorial below to keep your implementation Python-focused, since we believe it is involves approximately the same amount of effort to implement it slightly more naively in C.

In [2]:
import numpy as np
np.flip([[1,2,3],
        [4,5,6]])

array([[6, 5, 4],
       [3, 2, 1]])

Use this array as reference for the other examples:

In [8]:
A = np.arange(1, 25).reshape(3, 2, 4)  # 3，2，4
inspect_array(A, is_a_copy_of=A)

Data: |( 1  2  3  4) ( 5  6  7  8)|  |( 9 10 11 12) (13 14 15 16)|  |(17 18 19 20) (21 22 23 24)|
Offset: 0
Strides: 8, 4, 1


In [10]:
A

array([[[ 1,  2,  3,  4],
        [ 5,  6,  7,  8]],

       [[ 9, 10, 11, 12],
        [13, 14, 15, 16]],

       [[17, 18, 19, 20],
        [21, 22, 23, 24]]])

We have put brackets around each axis of the array. Notice that for this array, the offset is 0 and the strides are all positive.

----------------------------------------------------------

See what happens when you flip the array along the last axis below. 
Note that the `inspect_array` function compacts the array after flipping it so you can see the
"logical" order of the data, and the offset is calculated by comparing the address of the **non**-compacted
flipped array with that of `is_copy_of`, i.e., the array `A` we looked at above.

That is, we are looking at how numpy calculates the strides and offset for flipped arrays in order
to copy this behavior in our own implementation.

In [11]:
inspect_array(np.flip(A, (2,)), is_a_copy_of=A)  # 沿最后一维flip。
                                                 # 其他各维度strides不变，但最后一维相邻内存43，逻辑上反向
                                                 # 初始是4，首维的最后元素。offset=(shape[2]-1)*strides[2]

Data: |( 4  3  2  1) ( 8  7  6  5)|  |(12 11 10  9) (16 15 14 13)|  |(20 19 18 17) (24 23 22 21)|
Offset: 3
Strides: 8, 4, -1


So flipping the last axis reverses the order of the elements within each 4-dimensional "cell", as you can see above. The stride corresponding to the axis we flipped has been negated. And the offset is 3 -- this makes sense, e.g., because we want the new "first" element of the array to be 4, which was at index 3 in `A`.

In [12]:
inspect_array(np.flip(A, (1,)), is_a_copy_of=A) # 沿中间维filp
                                                # 其他各维度strides不变，但维度1相邻内存51，逻辑上反向
                                                # 初始元素offset=(shape[1]-1)*strides[1]

Data: |( 5  6  7  8) ( 1  2  3  4)|  |(13 14 15 16) ( 9 10 11 12)|  |(21 22 23 24) (17 18 19 20)|
Offset: 4
Strides: 8, -4, 1


Again for the middle axis: we negate the middle stride, and the offset is 4, which seems reasonable since we now want the first element to be 5, which was at index 4 in the original array `A`. 

In [13]:
inspect_array(np.flip(A, (0,)), is_a_copy_of=A) # offset=(shape[0]-1)*strides[0]

Data: |(17 18 19 20) (21 22 23 24)|  |( 9 10 11 12) (13 14 15 16)|  |( 1  2  3  4) ( 5  6  7  8)|
Offset: 16
Strides: -8, 4, 1


Try to infer the more general algorithm for computing the offset given the axis to flip.

----------------------------------------------------------------------------------------------------------

Observe what happens when we flip _all_ axes.

In [14]:
inspect_array(np.flip(A, (0,1,2)), is_a_copy_of=A) # offset= 最后一个元素(i,j,k)的offset （shape[0]-1,shape[1]-1.shape[2]-1） 
                                                   #         = (shape[0]-1)*strides[0] +(shape[1]-1)*strides[1]+(shape[2]-1)*strides[2]

Data: |(24 23 22 21) (20 19 18 17)|  |(16 15 14 13) (12 11 10  9)|  |( 8  7  6  5) ( 4  3  2  1)|
Offset: 23
Strides: -8, -4, -1


As mentioned earlier, the offset is then sufficient to point to the last element of the array, and this is just the "reverse order" version of `A`.

When we flip just axes 1 and 0...

In [15]:
inspect_array(np.flip(A, (0,1)), is_a_copy_of=A) # strides只是翻转对应维度
                                                 # flip后，首元素在offset中的偏移，是要翻转的维度i,j对应偏移之和
                                                 #  (shape[i]-1)*strides[i] +(shape[j]-1)*strides[j]

Data: |(21 22 23 24) (17 18 19 20)|  |(13 14 15 16) ( 9 10 11 12)|  |( 5  6  7  8) ( 1  2  3  4)|
Offset: 20
Strides: -8, -4, 1


The offset is 20. Looking back on our previous offset computations, do you notice something?

-------------------

With this exploration of numpy's ndarray flipping functionality, which uses negative strides and a custom offset,
try to implement `flip` in `ndarray.py`. You also must implement "flip" forward and backward functions in `ops.py`; note that these should be extremely short.

**Important:** You should call NDArray.make with the new strides and offset, and then immediately `.compact()` this array. The resulting array is then copied and has positive strides. We want this (less-than-optimal) behavior because we did not account for negative strides in our previous implementation. _Aside:_ If you want, consider where/if negative strides break your implementation. `__getitem__` definitely doesn't work due to how we processed slices; is there anything else? (_Note_: this isn't graded.)

Also, if you want to instead add a `flip` operator on the CPU/CUDA backends, that's also okay.



In [1]:
!python3 -m pytest -l -v -k "flip"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1803 items / 1763 deselected / 40 selected                           

tests/test_conv.py::test_flip_forward[params0-needle.backend_ndarray.ndarray_backend_cpu] PASSED [  2%]
tests/test_conv.py::test_flip_forward[params0-needle.backend_ndarray.ndarray_backend_cuda] PASSED [  5%]
tests/test_conv.py::test_flip_forward[params1-needle.backend_ndarray.ndarray_backend_cpu] PASSED [  7%]
tests/test_conv.py::test_flip_forward[params1-needle.backend_ndarray.ndarray_backend_cuda] PASSED [ 10%]
tests/test_conv.py::test_flip_forward[params2-needle.backend_ndarray.ndarray_backend_cpu] PASSED [ 12%]
tests/test_conv.py::test_flip_forward[params2-needle.backend_ndarray.ndarray_backend_cuda] PASSED [ 15%]
tests/test_c

-------------------------------------

### Dilation


The dilation operator puts zeros between elements of an ndarray. We will need it for computing the backward pass of convolution when the stride of the convolution is greater than 1. As an example, dilation should do the following to a 2x2 matrix when dilated by 1 on both axes:

$$
\begin{bmatrix}
1 & 2 \\
3 & 4
\end{bmatrix}
\Longrightarrow
\begin{bmatrix}
1 & 0 & 2 & 0 \\
0 & 0 & 0 & 0 \\
3 & 0 & 4 & 0 \\
0 & 0 & 0 & 0
\end{bmatrix}
$$

To get some intuition for why we need dilation for the backward pass of strided convolution, consider a  `stride=2`, `padding="same"`, `input_channels=output_channels=8` convolution applied to an input of size (10, 32, 32, 8). The resulting output will be of size (10, 16, 16, 8) due to the stride, and thus `out_grad` will have shape (10, 16, 16, 8). Yet, the gradient of the input needs to, of course, have shape (10, 32, 32, 8) -- so we must need to increase the size of `out_grad` in some way. Consider also that you could implement strided convolution as `Conv(x)[:, ::2, ::2, :]`, i.e., only keeping every other pixel in the spatial dimension.


Implement `Dilate` in `ops.py`. This function takes two additional parameters (in attrs): the `dilation` amount and the `axes` to dilate. You must also implement the corresponding op `UnDilate`, whose forward pass will be used to implement the gradient of `Dilate`. (This is so we do not have to implement `GetItem` and `SetItem` ops, which can be highly inefficient to backprop through without additional optimizations.)

In [4]:
!python3 -m pytest -l -v -k "dilate"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1803 items / 1777 deselected / 26 selected                           

tests/test_conv.py::test_dilate_forward[needle.backend_ndarray.ndarray_backend_cpu] PASSED [  3%]
tests/test_conv.py::test_dilate_forward[needle.backend_ndarray.ndarray_backend_cuda] PASSED [  7%]
tests/test_conv.py::test_dilate_backward[params0-needle.backend_ndarray.ndarray_backend_cpu] PASSED [ 11%]
tests/test_conv.py::test_dilate_backward[params0-needle.backend_ndarray.ndarray_backend_cuda] PASSED [ 15%]
tests/test_conv.py::test_dilate_backward[params1-needle.backend_ndarray.ndarray_backend_cpu] PASSED [ 19%]
tests/test_conv.py::test_dilate_backward[params1-needle.backend_ndarray.ndarray_backend_cuda] PASSED [ 23%]
tests/test_c

---------------------------------------

### Submit new ops (flip/dilation) to mugrade [10 points]

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "new_ops"

-----------------

### Convolution forward

Implement the forward pass of 2D multi-channel convolution in `ops.py`. You should probably refer to [this notebook](https://github.com/dlsyscourse/public_notebooks/blob/main/convolution_implementation.ipynb) from lecture, which implements 2D multi-channel convolution using im2col in numpy.

**Note:** Your convolution op should accept tensors in the NHWC format, as in the example above, and weights in the format (kernel_size, kernel_size, input_channels, output_channels).

However, you will need to add two additional features. Your convolution function should accept arguments for `padding` (default 0) and `stride` (default 1). For `padding`, you should simply apply your padding function to the spatial dimensions (i.e., axes 1 and 2). 

Implementing strided convolution should consist of a relatively small set of changes to your plain convolution implementation.

We recommend implementing convolution without stride first, ensuring you pass some of the tests below, and then adding in stride.

In [19]:
!python3 -m pytest -l -v -k "op_conv and forward"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1803 items / 1769 deselected / 34 selected                           

tests/test_conv.py::test_op_conv[forward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape0-W_shape0-1-0] PASSED [  2%]
tests/test_conv.py::test_op_conv[forward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape1-W_shape1-1-1] PASSED [  5%]
tests/test_conv.py::test_op_conv[forward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape2-W_shape2-1-2] PASSED [  8%]
tests/test_conv.py::test_op_conv[forward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape3-W_shape3-1-0] PASSED [ 11%]
tests/test_conv.py::test_op_conv[forward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape4-W_shape4-1-0] PASSED [ 14%]
tests/test_conv.py::test_op_conv[f

In [15]:
5//2

2

-----------------

### Convolution backward

Finding the gradients of 2D multi-channel convolution can be technically quite challenging (especially "rigorously"). We will try to provide some useful hints here. Basically, we encourage you to make use of the surprising fact that _whatever makes the dimensions work out is typically right_.

Ultimately, the backward pass of convolution can be done in terms of the convolution operator itself, with some clever manipulations using `flip`, `dilate`, and multiple applications of `transpose` to both the arguments and the results.

In the last section, we essentially implemented convolution as a matrix product: ignoring the various restride and reshape operations, we basically have something like `X @ W`, where `X` is the input and `W` is the weight. We also have `out_grad`, which is the same shape as `X @ W`. Now, you have already implemented the backward pass of matrix multiplication in a previous assignment, and we can use this knowledge to get some insight into the backward pass of convolution. In particular, referencing your matmul backward implementation, you may notice (heuristically speaking here):

`X.grad = out_grad @ W.transpose` \
`W.grad = X.transpose @ out_grad`

Surprisingly enough, things work out if we just assume that these are also convolutions (and now assuming that `out_grad`, `W`, and `X` are tensors amenable to 2D multi-channel convolution instead of matrices):

`X.grad = ≈conv(≈out_grad, ≈W)` \
`W.grad = ≈conv(≈X, ≈out_grad)`

In which the "≈" indicates that you need to apply some additional operators to these terms in order to get the dimensions to work out, such as permuting/transposing axes, dilating, changing the `padding=` argument to the convolution function, or permuting/transposing axes of the resulting convolution.

As we saw on the [last few slides here](https://dlsyscourse.org/slides/conv_nets.pdf) in class, the transpose of a convolution can be found by simply flipping the kernel. Since we're working in 2D instead of 1D, this means flipping the kernel both vertically and horizontally (thus why we implemented `flip`).

Summarizing some hints for both `X.grad` and `W.grad`:

`X.grad`
- The convolution of `out_grad` and `W`, with some operations applied to those
- `W` should be flipped over both the kernel dimensions
- If the convolution is strided, increase the size of `out_grad` with a corresponding dilation
- Do an example to analyze dimensions: note the shape you want for `X.grad`, and think about how you must permute/transpose the arguments and add padding to the convolution to achieve this shape 
    - This padding depends on both the kernel size and the `padding` argument to the convolution

`W.grad`
- The convolution of `X` and `out_grad`, with some operations applied to those
- The gradients of `W` must be accumulated over the batches; how can you make the conv operator itself do this accumulation?
    - Consider turning batches into channels via transpose/permute
- Analyze dimensions: how can you modify `X` and `out_grad` so that the shape of their convolution matches the shape of `W`? You may need to transpose/permute the result.
    - Remember to account for the `padding` argument passed to convolution

General tips
- Deal with strided convolutions last (you should be able to just drop in `dilate` when you've passed most of the tests)
- Start with the case where `padding=0`, then consider changing `padding` arguments
- You can "permute" axes with multiple calls to `transpose`

It might also be useful to skip ahead to nn.Conv, pass the forward tests, and then use both the tests below and the nn.Conv backward tests to debug your implementation.

In [1]:
!python3 -m pytest -l -v -k "op_conv and backward"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1745 deselected / 10 selected                           

tests/test_conv.py::test_op_conv[backward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape0-W_shape0-1-0] PASSED [ 10%]
tests/test_conv.py::test_op_conv[backward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape1-W_shape1-1-0] PASSED [ 20%]
tests/test_conv.py::test_op_conv[backward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape2-W_shape2-1-0] PASSED [ 30%]
tests/test_conv.py::test_op_conv[backward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape3-W_shape3-1-0] PASSED [ 40%]
tests/test_conv.py::test_op_conv[backward-needle.backend_ndarray.ndarray_backend_cpu-Z_shape4-W_shape4-1-0] PASSED [ 50%]
tests/test_conv.py::test_op_c

-----------------

### nn.Conv

#### Fixing init._calculate_fans for convolution
Previously, we have implemented Kaiming uniform/normal initializations, where we essentially assigned `fan_in = input_size` and `fan_out = output_size`.
For convolution, this becomes somewhat more detailed, in that you should multiply both of these by the "receptive field size", which is in this case just the product of the kernel sizes -- which in our case are always going to be the same, i.e., $k\times k$ kernels.

**You will need to edit your `kaiming_uniform`, etc. init functions to support multidimensional arrays.** In particular, you should add a new `shape` argument which is then passed to, e.g., the underlying `rand` function.

You can test this below; though it is not _directly_ graded, it must match ours to pass the nn.Conv mugrade tests.

In [47]:
!python3 -m pytest -l -v -k "kaiming_uniform"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1753 deselected / 2 selected                            

tests/test_conv.py::test_init_kaiming_uniform[needle.backend_ndarray.ndarray_backend_cpu] PASSED [ 50%]
tests/test_conv.py::test_init_kaiming_uniform[needle.backend_ndarray.ndarray_backend_cuda] PASSED [100%]

====================== 2 passed, 1753 deselected in 1.03s ======================


#### Implementing nn.Conv

Essentially, nn.Conv is just a wrapper of the convolution operator we previously implemented
which adds a bias term, initializes the weight and bias, and ensures that the padding is set so that the input and output dimensions are the same (in the `stride=1` case, anyways). 

Importantly, nn.Conv should support NCHW format instead of NHWC format. In particular, we think this makes more sense given our current BatchNorm implementation. You can implement this by applying `transpose` twice to both the input and output.  

- Ensure nn.Conv works for (N, C, H, W) tensors even though we implemented the conv op for (N, H, W, C) tensors
- Initialize the (k, k, i, o) weight tensor using Kaiming uniform initialization with default settings
- Initialize the (o,) bias tensor using uniform initialization on the interval $\pm$`1.0/(in_channels * kernel_size**2)**0.5`
- Calculate the appropriate padding to ensure input and output dimensions are the same
- Calculate the convolution, then add the properly-broadcasted bias term if present

You can now test your nn.Conv against PyTorch's nn.Conv2d with the two PyTest calls below.

In [2]:
!python3 -m pytest -l -v -k "nn_conv_forward"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1745 deselected / 10 selected                           

tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cpu-4-8-16-3-1] PASSED [ 10%]
tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cpu-32-8-16-3-2] PASSED [ 20%]
tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cpu-32-8-8-3-2] PASSED [ 30%]
tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cpu-32-16-8-3-1] PASSED [ 40%]
tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cpu-32-16-8-3-2] PASSED [ 50%]
tests/test_conv.py::test_nn_conv_forward[needle.backend_ndarray.ndarray_backend_cuda-4

In [4]:
!python3 -m pytest -l -v -k "nn_conv_backward"

-----------------

### Submit nn.Conv to mugrade [20 points]

In [6]:
#!python3 -m mugrade submit _1wNPXusjlWR2gMjyo9we -k "conv_forward"

In [58]:
#!python3 -m mugrade submit "YOUR KEY HERE" -k "conv_backward"

------------------------------------------------

### Implementing "ResNet9"

You will now use your convolutional layer to implement a model similar to _ResNet9_, which is known to be a reasonable model for getting good accuracy on CIFAR-10 quickly (see [here](https://github.com/davidcpage/cifar10-fast)). Our main change is that we used striding instead of pooling and divided all of the channels by 4 for the sake of performance (as our framework is not as well-optimized as industry-grade frameworks).

In the figure below, before the linear layer, you should "flatten" the tensor. We have added a module called `Flatten` in `nn.py` that you can complete and use, or you can simply use `.reshape` in the `forward()` method of your ResNet9.

Make sure that you pass the device to all modules in your model; otherwise, you will get errors about mismatched devices when trying to run with CUDA.

<center><img src="https://github.com/dlsyscourse/hw4/blob/main/ResNet9.png?raw=true" alt="ResNet9" style="width: 400px;" /></center>

We have tried to make it easier to pass the tests here than for previous assignments where you have implemented models. In particular, we are just going to make sure it has the right number of parameters and similar accuracy and loss after 1 or 2 batches of CIFAR-10.

In [38]:
!python3 -m pytest -l -v -k "resnet9"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1753 deselected / 2 selected                            

tests/test_conv.py::test_resnet9[needle.backend_ndarray.ndarray_backend_cpu] PASSED [ 50%]
tests/test_conv.py::test_resnet9[needle.backend_ndarray.ndarray_backend_cuda] PASSED [100%]

====================== 2 passed, 1753 deselected in 1.06s ======================


In [24]:
import numpy as np
a=np.zeros(5)
np.broadcast_to(a,(3,5))

array([[0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0.]])

### Submit ResNet9 to mugrade [10 points]

In [60]:
#!python3 -m mugrade submit "YOUR KEY HERE" -k "resnet9"

In [50]:
0.01**0

1.0

-----------------

Now, you can train your model on CIFAR-10 using the following code. Note that this is likely going to be quite slow, and also  not all that accurate due to the lack of data augmentation. You should expect it to take around 500s per epoch.

In [48]:
import sys
#sys.path.append('./python')
#sys.path.append('./apps')
import needle as ndl
from models import ResNet9
from simple_training import train_cifar10, evaluate_cifar10

device = ndl.cpu()
dataset = ndl.data.CIFAR10Dataset("data/cifar-10-batches-py", train=True)  # 自己实现的getitem,__len__

# 自己实现的迭代器。实现了__iter__，__next__方法，作用于dataset
dataloader = ndl.data.DataLoader(\
         dataset=dataset,
         batch_size=128,
         shuffle=True,
         #collate_fn=ndl.data.collate_ndarray,
         #device=device,
         #dtype="float32"
        )
model = ResNet9(device=device, dtype="float32")    # 基于自己的nn。参数都是Tensor。Tensor间交互，构建在自己的op和底层NDarray上。底层Array实现strides,shape等抽象，但封装了自己的cuda,c++算子
train_cifar10(model, dataloader, n_epochs=10, optimizer=ndl.optim.Adam,
      lr=0.001, weight_decay=0.001)
#evaluate_cifar10(model, dataloader)

NotImplementedError: 

## Part 4: Recurrent neural network [10 points]

**Note:** In the following sections, you may find yourself wanting to index into tensors, i.e., to use getitem or setitem. However, we have not implemented these for tensors in our library; instead, you should use `stack` and `split` operations.

In `python/needle/nn.py`, implement `RNNCell`.

$h^\prime = \text{tanh}(xW_{ih} + b_{ih} + hW_{hh} + b_{hh})$. If nonlinearity is 'relu', then ReLU is used in place of tanh.

All weights and biases should be initialized from $\mathcal{U}(-\sqrt{k}, \sqrt{k})$ where $k=\frac{1}{\text{hidden_size}}$.

In `python/needle/nn.py`, implement `RNN`.

For each element in the input sequence, each layer computes the following function:

$h_t = \text{tanh}(x_tW_{ih} + b_{ih} + h_{(t-1)}W_{hh} + b_{hh})$

where $h_t$ is the hidden state at time $t$, $x_t$ is the input at time $t$, and $h_{(t-1)}$ is the hidden state of the previous layer at time $t-1$ or the initial hidden state at time $0$. If nonlinearity is 'relu', then ReLU is used in place of tanh.

In a multi-layer RNN, the input $x_t^{(l)}$ of the $l$-th layer ($l \ge 2$) is the hidden state $h_t^{(l-1)}$ of the previous layer. 


In [23]:
!python3 -m pytest -l -v -k "test_rnn"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1115 deselected / 640 selected                          

tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-1-1-1] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-1-1-15] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-1-11-1] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-1-11-15] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-12-1-1] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-12-1-15] PASSED [  0%]
tests/test_sequence_models.py::test_rnn_cell[cpu-tanh-True-True-12-11-1] PASSED [  1%]
tests/test_sequence_models.py::test

tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-True-False-1-11-15] FAILED [ 11%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-True-False-12-1-1] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-True-False-12-1-15] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-True-False-12-11-1] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-True-False-12-11-15] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-1-1-1] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-1-1-15] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-1-11-1] PASSED [ 12%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-1-11-15] PASSED [ 13%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-12-1-1] PASSED [ 13%]
tests/test_sequence_models.py::test_rnn_cell[cuda-tanh-False-True-12-1-15] PASSED [ 13%]
tests/test_sequence_models

tests/test_sequence_models.py::test_rnn[cpu-tanh-True-True-12-11-1-2-13] PASSED [ 24%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-True-12-11-15-1-1] PASSED [ 24%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-True-12-11-15-1-13] PASSED [ 24%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-True-12-11-15-2-1] PASSED [ 24%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-True-12-11-15-2-13] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-1-1-1] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-1-1-13] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-1-2-1] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-1-2-13] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-15-1-1] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-True-False-1-1-15-1-13] PASSED [ 25%]
tests/test_sequence_models.py::test_rnn[cpu-tanh

tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-1-11-1-2-13] PASSED [ 36%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-1-11-15-1-1] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-1-11-15-1-13] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-1-11-15-2-1] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-1-11-15-2-13] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-1-1-1] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-1-1-13] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-1-2-1] PASSED [ 37%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-1-2-13] PASSED [ 38%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-15-1-1] PASSED [ 38%]
tests/test_sequence_models.py::test_rnn[cpu-tanh-False-False-12-1-15-1-13] PASSED [ 38%]
tests/test_sequence_models.py::

tests/test_sequence_models.py::test_rnn[cpu-relu-True-False-12-11-15-1-1] PASSED [ 49%]
tests/test_sequence_models.py::test_rnn[cpu-relu-True-False-12-11-15-1-13] PASSED [ 49%]
tests/test_sequence_models.py::test_rnn[cpu-relu-True-False-12-11-15-2-1] PASSED [ 49%]
tests/test_sequence_models.py::test_rnn[cpu-relu-True-False-12-11-15-2-13] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-1-1-1] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-1-1-13] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-1-2-1] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-1-2-13] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-15-1-1] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-15-1-13] PASSED [ 50%]
tests/test_sequence_models.py::test_rnn[cpu-relu-False-True-1-1-15-2-1] PASSED [ 51%]
tests/test_sequence_models.py::test_rnn[cpu-r

...

        """Create a new NDArray with the given properties.  This will allocation the
        memory if handle=None, otherwise it will use the handle of an existing
        array."""
        # 新建一个NDarray(new一个)并返回。
        # 如果没有指定底层数据，就会在指定device上新分配一个内存（device上的Array结构，通过pybind11绑定，作为handle），备用。是一维连续内存
        # 如果传入了底层数据（handle Array），不分配新内存。底层数据直接用给定的handle.(只是shape等参数变了)，设定新的shape, strides（未指定默认连续）, offset(默认0)，device
        # 尽量用这个函数。不修改底层内存的情况下，新建共享相同handle的NDarray(逻辑矩阵)
        array = NDArray.__new__(NDArray)
        array._shape = tuple(shape)
        array._strides = NDArray.compact_strides(shape) if strides is None else strides
        array._offset = offset
        array._device = device if device is not None else default_device()
        if handle is None:
>           array._handle = array.device.Array(prod(shape))  # 本质是device中的Array对象。这时候只有默认初始值
E           RuntimeError: an illegal memory access was encountered

array      = <[AttributeError("'NDArray' object has no at

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("input_size", INPUT_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("bias", BIAS)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("nonlinearity", NONLINEARITIES)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_rnn(seq_length, num_layers, batch_size, input_size, hidden_size, bias, init_hidden, nonlinearity, device):
        x = np.random.randn(seq_length, batch_size, input_size).astype(np.float32)
        h0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
    
        model_ = torch.nn.RNN(input_size, hidden_size, num_layers=num_layers, bias=bias, nonlinearity=nonlinearity)
        if init_hidden:
            output_, h_ = model_(torch.tensor(x), torch

    @staticmethod
    def make(shape, strides=None, device=None, handle=None, offset=0):
        """Create a new NDArray with the given properties.  This will allocation the
        memory if handle=None, otherwise it will use the handle of an existing
        array."""
        # 新建一个NDarray(new一个)并返回。
        # 如果没有指定底层数据，就会在指定device上新分配一个内存（device上的Array结构，通过pybind11绑定，作为handle），备用。是一维连续内存
        # 如果传入了底层数据（handle Array），不分配新内存。底层数据直接用给定的handle.(只是shape等参数变了)，设定新的shape, strides（未指定默认连续）, offset(默认0)，device
        # 尽量用这个函数。不修改底层内存的情况下，新建共享相同handle的NDarray(逻辑矩阵)
        array = NDArray.__new__(NDArray)
        array._shape = tuple(shape)
        array._strides = NDArray.compact_strides(shape) if strides is None else strides
        array._offset = offset
        array._device = device if device is not None else default_device()
        if handle is None:
>           array._handle = array.device.Array(prod(shape))  # 本质是device中的Array对象。这时候只有默认初始值
E           RuntimeError: an illegal

shape      = (1, 12)
strides    = None

python/needle/backend_ndarray/ndarray.py:164: RuntimeError
__________________ test_rnn[cuda-relu-False-False-12-1-1-2-1] __________________

seq_length = 1, num_layers = 2, batch_size = 1, input_size = 1, hidden_size = 12
bias = False, init_hidden = False, nonlinearity = 'relu', device = cuda()

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("input_size", INPUT_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("bias", BIAS)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("nonlinearity", NONLINEARITIES)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_rnn(seq_length, num_layers, batch_size, input_size, hidden_size, bias, init_hidden, nonlinearity, device):
        x = np.random.randn(seq

    @staticmethod
    def make(shape, strides=None, device=None, handle=None, offset=0):
        """Create a new NDArray with the given properties.  This will allocation the
        memory if handle=None, otherwise it will use the handle of an existing
        array."""
        # 新建一个NDarray(new一个)并返回。
        # 如果没有指定底层数据，就会在指定device上新分配一个内存（device上的Array结构，通过pybind11绑定，作为handle），备用。是一维连续内存
        # 如果传入了底层数据（handle Array），不分配新内存。底层数据直接用给定的handle.(只是shape等参数变了)，设定新的shape, strides（未指定默认连续）, offset(默认0)，device
        # 尽量用这个函数。不修改底层内存的情况下，新建共享相同handle的NDarray(逻辑矩阵)
        array = NDArray.__new__(NDArray)
        array._shape = tuple(shape)
        array._strides = NDArray.compact_strides(shape) if strides is None else strides
        array._offset = offset
        array._device = device if device is not None else default_device()
        if handle is None:
>           array._handle = array.device.Array(prod(shape))  # 本质是device中的Array对象。这时候只有默认初始值
E           RuntimeError: an illegal

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "rnn"

## Part 5: Long short-term memory network [10 points]
Implement - `Sigmoid`

$\sigma(x) = \frac{1}{1 + \text{exp}(-x)}$

In `python/needle/nn.py`, implement `Sigmoid`, `LSTMCell` and `LSTM`.

\begin{align}
i &= \sigma(xW_{ii} + b_{ii} + hW_{hi} + b_{hi}) \\
f &= \sigma(xW_{if} + b_{if} + hW_{hf} + b_{hf}) \\
g &= \text{tanh}(xW_{ig} + b_{ig} + hW_{hg} + b_{hg}) \\
o &= \sigma(xW_{io} + b_{io} + hW_{ho} + b_{ho}) \\
c^\prime &= f * c + i * g \\
h^\prime &= o * \text{tanh}(c^\prime)
\end{align}

where $\sigma$ is the sigmoid function, and $i$, $f$, $g$, $o$ are the input, forget, cell, and output gates, respectively. 

All weights and biases should be initialized from $\mathcal{U}(-\sqrt{k}, \sqrt{k})$ where $k=\frac{1}{\text{hidden_size}}$.

Now implement `LSTM` in `python/needle/nn.py`, which applies a multi-layer LSTM RNN to an input sequence. For each element in the input sequence, each layer computes the following function:

\begin{align}
i_t &= \sigma(x_tW_{ii} + b_{ii} + h_{(t-1)}W_{hi} + b_{hi}) \\
f_t &= \sigma(x_tW_{if} + b_{if} + h_{(t-1)}W_{hf} + b_{hf}) \\
g_t &= \text{tanh}(x_tW_{ig} + b_{ig} + h_{(t-1)}W_{hg} + b_{hg}) \\
o_t &= \sigma(x_tW_{io} + b_{io} + h_{(t-1)}W_{ho} + b_{ho}) \\
c_t &= f * c_{(t-1)} + i * g \\
h_t &= o * \text{tanh}(c_t)
\end{align},
where $h_t$ is the hidden state at time $t$, $c_t$ is the cell state at time $t$, $x_t$ is the input at time $t$, $h_{(t-1)}$ is the hidden state of the layer at time $t-1$ or the initial hidden state at time $0$, and $i_t$, $f_t$, $g_t$, $o_t$ are the input, forget, cell, and output gates at time $t$ respectively. 

In a multi-layer LSTM, the input $x_t^{(l)}$ of the $l$-th layer ($l \ge 2$) is the hidden state $h_t^{(l-1)}$ of the previous layer. 

In [28]:
!python3 -m pytest -l -v -k "test_lstm"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1435 deselected / 320 selected                          

tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-1-1-1] PASSED [  0%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-1-1-15] PASSED [  0%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-1-11-1] PASSED [  0%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-1-11-15] PASSED [  1%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-12-1-1] PASSED [  1%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-12-1-15] PASSED [  1%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-12-11-1] PASSED [  2%]
tests/test_sequence_models.py::test_lstm_cell[cpu-True-True-12-

tests/test_sequence_models.py::test_lstm[cpu-True-True-1-11-15-1-13] PASSED [ 24%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-1-11-15-2-1] PASSED [ 24%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-1-11-15-2-13] PASSED [ 25%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-1-1-1] PASSED [ 25%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-1-1-13] PASSED [ 25%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-1-2-1] PASSED [ 25%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-1-2-13] PASSED [ 26%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-15-1-1] PASSED [ 26%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-15-1-13] PASSED [ 26%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-15-2-1] PASSED [ 27%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-1-15-2-13] PASSED [ 27%]
tests/test_sequence_models.py::test_lstm[cpu-True-True-12-11-1-1-1] PASSED [ 27%]
tests/test_seq

tests/test_sequence_models.py::test_lstm[cpu-False-True-12-11-15-2-13] PASSED [ 50%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-1-1-1] PASSED [ 50%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-1-1-13] PASSED [ 50%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-1-2-1] PASSED [ 50%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-1-2-13] PASSED [ 51%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-15-1-1] PASSED [ 51%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-15-1-13] PASSED [ 51%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-15-2-1] PASSED [ 52%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-1-15-2-13] PASSED [ 52%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-11-1-1-1] PASSED [ 52%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-11-1-1-13] PASSED [ 53%]
tests/test_sequence_models.py::test_lstm[cpu-False-False-1-11-1-2-1] PASSED [ 53%]
t

tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-1-1-1] FAILED [ 75%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-1-1-13] FAILED [ 75%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-1-2-1] FAILED [ 75%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-1-2-13] FAILED [ 76%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-15-1-1] FAILED [ 76%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-15-1-13] FAILED [ 76%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-15-2-1] FAILED [ 77%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-1-15-2-13] FAILED [ 77%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-11-1-1-1] FAILED [ 77%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-11-1-1-13] FAILED [ 78%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-11-1-2-1] FAILED [ 78%]
tests/test_sequence_models.py::test_lstm[cuda-True-False-12-11-1-2-13] FAIL

    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("input_size", INPUT_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("bias", BIAS)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_lstm(seq_length, num_layers, batch_size, input_size, hidden_size, bias, init_hidden, device):
        x = np.random.randn(seq_length, batch_size, input_size).astype(np.float32)
        h0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
        c0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
    
        model_ = torch.nn.LSTM(input_size, hidden_size, bias=bias, num_layers=num_layers)
        if init_hidden:
            output_, (h_, c_) = model_(torch.tensor(x), (torch.tensor(h0), torch.tensor(c0)))
        else:
            output

...

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("input_size", INPUT_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("bias", BIAS)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_lstm(seq_length, num_layers, batch_size, input_size, hidden_size, bias, init_hidden, device):
        x = np.random.randn(seq_length, batch_size, input_size).astype(np.float32)
        h0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
        c0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
    
        model_ = torch.nn.LSTM(input_size, hidden_size, bias=bias, num_layers=num_layers)
        if init_hidden:
            output_, (h_, c_) = model_(torch.tensor(x), (torch.tensor(

    self.W_ih=Parameter(init.rand(input_size,4*hidden_size,low=-np.sqrt(k), high=np.sqrt(k), device=device, dtype=dtype))
        __class__  = <class 'needle.nn.LSTMCell'>
        bias       = False
        device     = cuda()
        dtype      = 'float32'
        hidden_size = 1
        input_size = 1
        k          = 1.0
        self       = <needle.nn.LSTMCell object at 0x7fa0002900d0>
python/needle/init.py:8: in rand
    array = device.rand(*shape, dtype=dtype) * (high - low) + low
        device     = cuda()
        dtype      = 'float32'
        high       = 1.0
        low        = -1.0
        requires_grad = False
        shape      = (1, 4)
python/needle/backend_ndarray/ndarray.py:45: in rand
    return NDArray(np.random.rand(*shape).astype(dtype), device=self)
        dtype      = 'float32'
        self       = cuda()
        shape      = (1, 4)
python/needle/backend_ndarray/ndarray.py:122: in __init__
    array = self.make(other.shape, device=device)             # make

    @staticmethod
    def make(shape, strides=None, device=None, handle=None, offset=0):
        """Create a new NDArray with the given properties.  This will allocation the
        memory if handle=None, otherwise it will use the handle of an existing
        array."""
        # 新建一个NDarray(new一个)并返回。
        # 如果没有指定底层数据，就会在指定device上新分配一个内存（device上的Array结构，通过pybind11绑定，作为handle），备用。是一维连续内存
        # 如果传入了底层数据（handle Array），不分配新内存。底层数据直接用给定的handle.(只是shape等参数变了)，设定新的shape, strides（未指定默认连续）, offset(默认0)，device
        # 尽量用这个函数。不修改底层内存的情况下，新建共享相同handle的NDarray(逻辑矩阵)
        array = NDArray.__new__(NDArray)
        array._shape = tuple(shape)
        array._strides = NDArray.compact_strides(shape) if strides is None else strides
        array._offset = offset
        array._device = device if device is not None else default_device()
        if handle is None:
>           array._handle = array.device.Array(prod(shape))  # 本质是device中的Array对象。这时候只有默认初始值
E           RuntimeError: an illegal

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("input_size", INPUT_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("bias", BIAS)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_lstm(seq_length, num_layers, batch_size, input_size, hidden_size, bias, init_hidden, device):
        x = np.random.randn(seq_length, batch_size, input_size).astype(np.float32)
        h0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
        c0 = np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32)
    
        model_ = torch.nn.LSTM(input_size, hidden_size, bias=bias, num_layers=num_layers)
        if init_hidden:
            output_, (h_, c_) = model_(torch.tensor(x), (torch.tensor(

    return NDArray(np.random.rand(*shape).astype(dtype), device=self)
        dtype      = 'float32'
        self       = cuda()
        shape      = (11, 48)
python/needle/backend_ndarray/ndarray.py:122: in __init__
    array = self.make(other.shape, device=device)             # make:按给定的shape,device，在device上开辟了一份连续内存。（strides连续）
        device     = cuda()
        other      = array([[0.2541967 , 0.2980798 , 0.01302311, 0.9550031 , 0.9283338 ,
        0.6357676 , 0.18229201, 0.6468828 , 0.2596....20261094, 0.5277604 , 0.20597845, 0.73891795, 0.5499415 ,
        0.43805018, 0.02274464, 0.91081834]], dtype=float32)
        self       = <[AttributeError("'NDArray' object has no attribute '_device'") raised in repr()] NDArray object at 0x7fa0005e5cd0>
_ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ 

shape = (11, 48), strides = None, device = cuda(), handle = None, offset = 0

    @staticmethod
    def make(shape, strides=None, device=None, handle=None, of

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "lstm"

## Part 6: Penn Treebank dataset [10 points]

In word-level language modeling tasks, the model predicts the probability of the next word in the sequence, based on the words already observed in the sequence. You will write support for the Penn Treebank dataset, which consists of stories from the Wall Street Journal, to train and evaluate a language model on word-level prediction.

In `python/needle/data.py`, start by implementing the `Dictionary` class, which creates a dictionary from a list of words, mapping each word to a unique integer.

Next, we will use this `Dictionary` class to create a corpus from the train and test txt files in the Penn Treebank dataset that you downloaded at the beginning of the notebook. Implement the `tokenize` function in the `Corpus` class to do this.

In order to prepare the data for training and evaluation, you will next implement the `batchify` function. Starting from sequential data, batchify arranges the dataset into columns. For instance, with the alphabet as the sequence and batch size 4, we'd get

```
┌ a g m s ┐
│ b h n t │
│ c i o u │
│ d j p v │
│ e k q w │
└ f l r x ┘
```

These columns are treated as independent by the model, which means that the dependence of e. g. 'g' on 'f' cannot be learned, but allows more efficient batch processing.

Next, implement the `get_batch` function. `get_batch` subdivides the source data into chunks of length `bptt`. If source is equal to the example output of the batchify function, with a bptt-limit of 2, we'd get the following two Variables for i = 0:
```
┌ a g m s ┐ ┌ b h n t ┐
└ b h n t ┘ └ c i o u ┘
```
Note that despite the name of the function, the subdivison of data is not done along the batch dimension (i.e. dimension 1), since that was handled by the batchify function. The chunks are along dimension 0, corresponding to the seq_len dimension in the LSTM or RNN.

In [30]:
# 原始dataset是L个T长序列
# 一般确定b后，每个batch是b个样本，（B,T）  一共n_b个batch
#
# 现在要把整个dataset输出成[n_b,B]。  
# 原来每个较长的样本，拆成B份。作为B个独立样本。对应B列
!python3 -m pytest -l -v -k "ptb"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1729 deselected / 26 selected                           

tests/test_cifar_ptb_data.py::test_cifar10_dataset[True] PASSED          [  3%]
tests/test_cifar_ptb_data.py::test_cifar10_dataset[False] PASSED         [  7%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-True-1] PASSED     [ 11%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-True-15] PASSED    [ 15%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-False-1] PASSED    [ 19%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cpu-False-15] PASSED   [ 23%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cuda-True-1] PASSED    [ 26%]
tests/test_cifar_ptb_data.py::test_cifar10_loader[cuda-True-15] PASSED   [ 30%]

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "ptb"

## Part 7: Training a word-level language model [10 points]

Finally, you will use the `RNN` and `LSTM` components you have written to construct a language model that we will train on the Penn Treebank dataset.

First, in `python/needle/nn.py` implement `Embedding`. Consider we have a dictionary with 1000 words. Then for a word which indexes into this dictionary, we can represent this word as a one-hot vector of size 1000, and then use a linear layer to project this to a vector of some embedding size.

In `apps/models.py`, you can now implement `LanguageModel`. Your language model should consist of 

- An embedding layer (which maps word IDs to embeddings) 
- A sequence model (either RNN or LSTM)
- A linear layer (which outputs probabilities of the next word)

In `apps/simple_training.py` implement `epoch_general_ptb`, `train_ptb`, and `evaluate_ptb`.

In [12]:
!python3 -m pytest -l -v -k "language_model_implementation"

============================= test session starts ==============================
platform linux -- Python 3.9.6, pytest-7.1.3, pluggy-1.0.0 -- /home/xuweijia/.conda/envs/pytorch1.9/bin/python3
cachedir: .pytest_cache
rootdir: /media/xuweijia/DATA/Courses/deep-Learning-System/hw4
collected 1755 items / 1243 deselected / 512 selected                          

tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-1-1-1] PASSED [  0%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-1-1-13] PASSED [  0%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-1-2-1] PASSED [  0%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-1-2-13] PASSED [  0%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-15-1-1] PASSED [  0%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-True-1-1-15-1-13] PASSED [  1%

tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1-False-12-34-15-2-13] PASSED [ 12%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-1-1-1] PASSED [ 12%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-1-1-13] PASSED [ 12%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-1-2-1] PASSED [ 13%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-1-2-13] PASSED [ 13%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-15-1-1] PASSED [ 13%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-15-1-13] PASSED [ 13%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-15-2-1] PASSED [ 13%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-rnn-1000-True-1-1-15-2-13] PASSED [ 14%]
tests/tes

tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1-False-12-34-15-2-1] FAILED [ 37%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1-False-12-34-15-2-13] FAILED [ 37%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-1-1-1] FAILED [ 37%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-1-1-13] FAILED [ 37%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-1-2-1] FAILED [ 38%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-1-2-13] FAILED [ 38%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-15-1-1] FAILED [ 38%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-15-1-13] FAILED [ 38%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-True-1-1-15-2-1] FAILED [ 38%]
t

tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-False-12-34-15-1-13] FAILED [ 49%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-False-12-34-15-2-1] FAILED [ 49%]
tests/test_sequence_models.py::test_language_model_implementation[cpu-lstm-1000-False-12-34-15-2-13] FAILED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-1-1-1] PASSED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-1-1-13] PASSED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-1-2-1] PASSED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-1-2-13] PASSED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-15-1-1] PASSED [ 50%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1-True-1-1-15-1-13] PASSED [ 51%]
tests/tes

tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1000-False-12-34-15-1-13] FAILED [ 74%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1000-False-12-34-15-2-1] FAILED [ 74%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-rnn-1000-False-12-34-15-2-13] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-1-1-1] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-1-1-13] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-1-2-1] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-1-2-13] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-15-1-1] FAILED [ 75%]
tests/test_sequence_models.py::test_language_model_implementation[cuda-lstm-1-True-1-1-15-1-13] FAILED [ 76%]
tes

...

    @pytest.mark.parametrize("embedding_size", EMBEDDING_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("output_size", OUTPUT_SIZES)
    @pytest.mark.parametrize("seq_model", SEQ_MODEL)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_language_model_implementation(seq_length, num_layers, batch_size, embedding_size, hidden_size,
                            init_hidden, output_size, seq_model, device):
        #TODO add test for just nn.embedding?
        x = np.random.randint(0, output_size, (seq_length, batch_size)).astype(np.float32)  # T,B
>       h0 = ndl.Tensor(np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32), device=device)

batch_size = 15
device     = cuda()
embedding_size = 34
hidden_size = 1
init_hidden = True
num_layers = 1
output_size = 1000
seq_length = 1
seq_model  = 'rnn'
x          = array([[389., 219., 786.,  44

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("embedding_size", EMBEDDING_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("output_size", OUTPUT_SIZES)
    @pytest.mark.parametrize("seq_model", SEQ_MODEL)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_language_model_implementation(seq_length, num_layers, batch_size, embedding_size, hidden_size,
                            init_hidden, output_size, seq_model, device):
        #TODO add test for just nn.embedding?
        x = np.random.randint(0, output_size, (seq_length, batch_size)).astype(np.float32)  # T,B
>       h0 = ndl.Tensor(np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32), device=device)

batch_size = 1
device     = cuda()

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("embedding_size", EMBEDDING_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("output_size", OUTPUT_SIZES)
    @pytest.mark.parametrize("seq_model", SEQ_MODEL)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_language_model_implementation(seq_length, num_layers, batch_size, embedding_size, hidden_size,
                            init_hidden, output_size, seq_model, device):
        #TODO add test for just nn.embedding?
        x = np.random.randint(0, output_size, (seq_length, batch_size)).astype(np.float32)  # T,B
>       h0 = ndl.Tensor(np.random.randn(num_layers, batch_size, hidden_size).astype(np.float32), device=device)

batch_size = 15
device     = cuda(

_____ test_language_model_implementation[cuda-rnn-1000-False-12-1-1-2-13] ______

seq_length = 13, num_layers = 2, batch_size = 1, embedding_size = 1
hidden_size = 12, init_hidden = False, output_size = 1000, seq_model = 'rnn'
device = cuda()

    @pytest.mark.parametrize("seq_length", SEQ_LENGTHS)
    @pytest.mark.parametrize("num_layers", NUM_LAYERS)
    @pytest.mark.parametrize("batch_size", BATCH_SIZES)
    @pytest.mark.parametrize("embedding_size", EMBEDDING_SIZES)
    @pytest.mark.parametrize("hidden_size", HIDDEN_SIZES)
    @pytest.mark.parametrize("init_hidden", INIT_HIDDEN)
    @pytest.mark.parametrize("output_size", OUTPUT_SIZES)
    @pytest.mark.parametrize("seq_model", SEQ_MODEL)
    @pytest.mark.parametrize("device", _DEVICES, ids=["cpu", "cuda"])
    def test_language_model_implementation(seq_length, num_layers, batch_size, embedding_size, hidden_size,
                            init_hidden, output_size, seq_model, device):
        #TODO add test for just nn.embedding?
 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
!python3 -m pytest -l -v -k "language_model_training"

In [ ]:
!python3 -m mugrade submit "YOUR KEY HERE" -k "language_model"

Now, you can train your language model on the Penn Treebank dataset:

In [ ]:
import needle as ndl
sys.path.append('./apps')
from models import LanguageModel
from simple_training import train_ptb, evaluate_ptb

device = ndl.cpu()
corpus = ndl.data.Corpus("data/ptb")
train_data = ndl.data.batchify(corpus.train, batch_size=16, device=ndl.cpu(), dtype="float32") # (T1,B)
model = LanguageModel(30, len(corpus.dictionary), hidden_size=10, num_layers=2, seq_model='rnn', device=ndl.cpu())
train_ptb(model, train_data, seq_len=1, n_epochs=1, device=device)
evaluate_ptb(model, train_data, seq_len=40, device=device)

In [ ]:
0